# GCD / Euclidean algorithm
Explaination: https://brilliant.org/wiki/extended-euclidean-algorithm/

In [1]:
# Returns the greatest common divisor of a and b.
def gcd(a, b):
    if b > a:
        return gcd(b, a)
    if a % b == 0:
        return b
    return gcd(b, a % b)

gcd(35,30)

5

# Back substitution / Extended euclidean algorithm
Explaination: https://brilliant.org/wiki/extended-euclidean-algorithm/

In [2]:
def gcdExtended(a, b):  
    # Base Case  
    if a == 0 :   
        return b,0,1

    gcd,x1,y1 = gcdExtended(b%a, a)

    # Update x and y using results of recursive call  
    x = y1 - (b//a) * x1  
    y = x1  

    return gcd,x,y 

a, b = 35,10
g, x, y = gcdExtended(a, b)
print(f"ax + by = gcd(a,b)    ==>    {a}*{x} + {b}*{y} = gcd({a},{b})\n")

print(f"gcd({a},{b}) = {g}")
print(f"x = {x}, y = {y}")

ax + by = gcd(a,b)    ==>    35*1 + 10*-3 = gcd(35,10)

gcd(35,10) = 5
x = 1, y = -3


# Modular inverse, A^-1
Explanation: https://www.khanacademy.org/computing/computer-science/cryptography/modarithmetic/a/modular-inverses

In [3]:
# Naive method of finding modular inverse for A (mod C) 
def inverse(a, c):
    for b in range(c):
        if (a*b)%c == 1: return b
    print("NO INVERSE FOUND")

a,c = 3,7
b = inverse(a,c)

print(f"{a} * {b} ≡ 1 (mod {c})")
print(f"Modular inverse for {a} (mod {c}) is {b}")
print(f"a^-1 = {b}")

3 * 5 ≡ 1 (mod 7)
Modular inverse for 3 (mod 7) is 5
a^-1 = 5


# Chineese remainder theorem
Source: https://rosettacode.org/wiki/Chinese_remainder_theorem#Python

In [4]:
from functools import reduce
def crt(n, a):
    sum = 0
    prod = reduce(lambda a, b: a*b, n)
    for n_i, a_i in zip(n, a):
        p = prod // n_i
        sum += a_i * mul_inv(p, n_i) * p
    return sum % prod

def mul_inv(a, b):
    b0 = b
    x0, x1 = 0, 1
    if b == 1: return 1
    while a > 1:
        q = a // b
        a, b = b, a%b
        x0, x1 = x1 - q * x0, x0
    if x1 < 0: x1 += b0
    return x1

n = [3, 5, 7]
a = [2, 3, 2]
print(crt(n, a))

23


# Euler function φ and Z*n
From slides 2020-4135-l07 - Number Theory for Public Key Cryptography

In [5]:
# Relatively prime means that gcd equals 1
def is_relative_prime(a,b):
    if b == 0 or a == 0: return False
    return gcd(a,b) == 1

# The set of positive integers less than n and relatively prime 
# to n form the reduced residue class Z∗n.
def z_star(n):
    r = []
    for i in range(1,n):
        if is_relative_prime(i,n):
            r.append(i)
    return r

n = 81
ar = z_star(n)
e = len(ar)
print(f"φ({n}) = {e} since the {e} items in Z*{n} are each relatively prime to {n}.")
print(f"Z*{n} = {ar}")

φ(81) = 54 since the 54 items in Z*81 are each relatively prime to 81.
Z*81 = [1, 2, 4, 5, 7, 8, 10, 11, 13, 14, 16, 17, 19, 20, 22, 23, 25, 26, 28, 29, 31, 32, 34, 35, 37, 38, 40, 41, 43, 44, 46, 47, 49, 50, 52, 53, 55, 56, 58, 59, 61, 62, 64, 65, 67, 68, 70, 71, 73, 74, 76, 77, 79, 80]


# Testing for primality
From slides 2020-4135-l07 - Number Theory for Public Key Cryptography

In [6]:
from math import sqrt
# Inefficient, but accurate method
def is_prime(n):
    if n % 2 == 0 and n > 2: 
        return False
    return all(n % i for i in range(3, int(sqrt(n)) + 1, 2))

print(137, is_prime(137))

137 True


In [7]:
# Fermat primality test

# Inputs: 
#    n: a value to test for primality;
#    k: a parameter that determines the number of 
#       times to test for primality
from random import randint
def fermat_prime(n, k):
    for x in range(k):
        a = randint(2,n-2)
        # Fermat’s theorem says that if a number p is prime then 
        # a^p−1 mod p = 1 for all a with gcd(a,p) = 1.
        if not (a**(n-1))%n == 1:
            return "composite"
    return "probable prime"

n = 1105 # value to test for primality;
k = 1 # number of times to test for primality

print(f"{n} is {fermat_prime(n,k)}")

# First few Carmichael numbers are: 561, 1105, 1729, 2465 
# Will output probable prime for every a with gcd(a, n) = 1

1105 is probable prime


## Miller-Rabin
From https://en.wikipedia.org/wiki/Miller%E2%80%93Rabin_primality_test  
This test is not fooled by Charmichael numbers.

To test `n`, you choose different `a` values, and test if 

> $a^{d*2^i} \equiv 1 \pmod{n}$ for $i = (0, 1, 2, ... r)$

If this happens, look at the congruence on the calculation just before you got `1`. If that value is not -1 (aka n-1), the value is composite aka not prime.

In [23]:
# Miller-Rabin primality test
# This test is not fooled by Charmichael numbers.

from math import log2, floor
from random import randint

def decompose_even_number(n):
    '''Find the values r and d such that n == d * 2**r.'''
    r = 0
    d = n
    for i in range(1, floor(log2(n)) + 1):
        if (d/2).is_integer():
            d = d/2
            r += 1
        else:
            break
    return (r, int(d))

verbose = False  # Print during execution

def miller_rabin_prime(n):
    ''':param n: should be odd, and n>3. No primes can be even, for obvious reasons.'''
    accuracy = 3  # How many different `a` to test
    r, d = decompose_even_number(n-1)  # n is odd, thus n-1 is even
    verbose and print(f"Testing {n} a maximum of {accuracy} times...")
    
    for _ in range(accuracy):
        try:
            a = randint(2, n-2)  # The "witness".  TODO: don't reuse a witness.
            verbose and print(f"\tTesting {n} with a={a}")

            x = (a**d) % n
            if x == 1 or x == n-1:
                verbose and print(f"\t({a}**{d})%{n} was 1 or -1 already!")
                continue # This witness was immediately 1 or -1 (aka n-1), so it can't help us any more.
            for squaring in range(r-1):
                x = (x**2) % n
                verbose and print(f"\tx={x}")
                if x == n-1:
                    raise Exception("Try next witness")  # This witness can't help any more.
            return "composite" # The witness didnt uphold the criteria for a prime, so n is composite!
        except Exception as tryNext:
            continue
    return "probably prime"
    
s, d = decompose_even_number(168)
print(f"168 = {d}*2^{s} = {d*(2**s)}")
s, d = decompose_even_number(65536)
print(f"65536 = {d}*2^{s} = {d*(2**s)}")
print()

for value in [16127, 561, 2465, 65537]:
    print(f"{value} is {miller_rabin_prime(value)}.")


168 = 21*2^3 = 168
65536 = 1*2^16 = 65536

16127 is probably prime.
561 is composite.
2465 is composite.
65537 is probably prime.


# Integer factorisation
Given an integer, find its prime factors

In [8]:
# Brute force solution
def prime_factors(n):
    i = 2
    factors = []
    while i * i <= n:
        if n % i:
            i += 1
        else:
            n //= i
            factors.append(i)
    if n > 1:
        factors.append(n)
    return factors

# Check if the numbers in array a is the factors of n
def factor_test(a, n):
    k = 1
    for i in factors:
        k=k*i
    return k==n

n = 641361
factors = prime_factors(n)
print(f"The factors of {n} are {factors}, {'verified' if factor_test(factors, n) else 'ERROR'}")

print("Manual test:", factor_test([3, 7, 7, 4363], 641361))

The factors of 641361 are [3, 7, 7, 4363], verified
Manual test: True


# Discrete logarithm problem
Given a prime `p` and an integer `y` with `0 < y < p`, find `x` such that 
```
y = g^x mod p
```

No polynomial algorithims exists, but "Baby-step giant-step" is a reasonable one. 

Sources:
- https://stackoverflow.com/a/1832648/5976426
- https://en.wikipedia.org/wiki/Baby-step_giant-step
- https://gist.github.com/0xTowel/b4e7233fc86d8bb49698e4f1318a5a73

In [35]:
from math import ceil, sqrt

def bsgs(g, y, p):
    '''
    Solve for x in y = g^x mod p given a prime p.
    If p is not prime, you shouldn't use BSGS anyway.
    '''
    N = ceil(sqrt(p - 1))  # phi(p) is p-1 if p is prime

    # Store hashmap of g^{1...m} (mod p). Baby step.
    tbl = {pow(g, i, p): i for i in range(N)}

    # Precompute via Fermat's Little Theorem
    c = pow(g, N * (p - 2), p)

    # Search for an equivalence in the table. Giant step.
    for j in range(N):
        h = (y * pow(c, j, p)) % p
        if h in tbl:
            return j * N + tbl[h]

    # Solution not found
    return None

def disc_log_test(y, g, x, p):
    return y == (g**x) % p

#y = 355407489
#g = 7894352216
#p = 604604729 # Must be prime

# y = g^x mod p
y = 34
g = 7324
p = 4363 # Must be prime

x = bsgs(g, y, p)

print(f"x = {x}")

print(f"y = g^x mod p    ==>    {y} = {g}^{x} mod {p}")

# Don't run the test with big numbers!
if x<10000: print(f"Test: {disc_log_test(y,g,x,p)}")

x = 2570
y = g^x mod p    ==>    34 = 7324^2570 mod 4363
Test: True


# Block ciphers

Notation:

- `P`: Plaintext block (length n bits) 
- `C`: Ciphertext block (length n bits) 
- `K` : Key (length k bits)
- `C = E(P, K)`: Encryption function 
- `P = D(C, K)`: Decryption function

In [10]:
# Discarded code

def z(n):
    return [i for i in range(n)]
print(z(10))

n = 81
zn = z(n)
rel_primes = list(filter(lambda x: is_relative_prime(x,n), zn))
print(len(rel_primes))

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
54
